In [1]:
%config Completer.use_jedi = False
from plotly.offline import init_notebook_mode, iplot
import plotly.graph_objects as go
import plotly.express as px
import cufflinks as cf
import torch
from train_mnistgan import Generator
from torchvision import transforms
import numpy as np
import random

init_notebook_mode(connected = True)

In [2]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu') 
gen = Generator().to(device)
gen.load_state_dict(torch.load('output/G-20.pth'))

<All keys matched successfully>

In [3]:
X = np.load("output/fvecs.npy")
Y = np.load("output/cls.npy")

from sklearn.decomposition import PCA

pca = PCA(n_components=2)
X1 = pca.fit_transform(X)

indx = Y==0
ref_min = X[indx][0]
indx = Y==2
ref_max = X[indx][0]

In [4]:
def ret_img(step, max_steps):
    vec = ref_min + (step * (ref_max - ref_min)/max_steps)
    vec = torch.tensor(vec).to(device)
    img = gen(vec.unsqueeze(0))
    img = img.view([1,32,32])
    img = transforms.ToPILImage()(img).convert('RGB')
    img = list(np.array(img))
    return img

In [5]:
max_steps = 100

fig = go.Figure()

for step in np.arange(0, max_steps, 1):
    fig.add_trace(go.Image(z = ret_img(step, max_steps)))
    
fig.data[10].visible = True

steps = []

for i in range(len(fig.data)):
    step = dict(
        method="update",
        args=[{"visible": [False] * len(fig.data)},
              {"title": "Slider switched to step: " + str(i)}]
    )
    step["args"][0]["visible"][i] = True 
    steps.append(step)

sliders = [dict(active=10, currentvalue={"prefix": "Frequency: "}, pad={"t": 50}, steps=steps)]

fig.update_layout(sliders = sliders)

fig.show()